<a href="https://colab.research.google.com/github/Ayrsz/SignalAndSistemyProject/blob/main/Augmentation_Audios.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [21]:
#Model CNN
import torch
import torch.nn as nn
import torchaudio

#Scientific computation
import numpy as np
import jax

#Plot and view
from matplotlib import pyplot as plt
import IPython as ipy
from IPython import display
from IPython.display import Audio

#Data manipulation
import pandas as pd
import scipy as sci
import os

#Audio manipulation
import librosa
import soundfile as sf

In [92]:
!pip install audiomentations pyroomacoustics

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.1/35.1 MB 35.4 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Using cached pybind11-2.13.6-py3-none-any.whl.metadata (9.5 kB)
Using cached pybind11-2.13.6-py3-none-any.whl (243 kB)
  Created wheel for pyroomacoustics: filename=pyroomacoustics-0.8.3-cp311-cp311-linux_x86_64.whl size=46837533 sha256=8ee579a4d54ed132aae16877bbf1741e4b23a4c8e1c169744909c5b0048e93b5
  Stored in directory: /root/.cache/pip/wheels/63/45/21/e7df2e64ca3b125fd4d6da69c8a4ee46d0ad6acc1f3de6832f
Successfully built pyroomacoustics


In [93]:
import audiomentations as audmen

In [94]:
from zipfile import ZipFile
from google.colab import drive
drive.mount("/content/drive", force_remount = True)

Mounted at /content/drive


In [17]:
#Unzip in a specific folder
path_zip = "/content/drive/MyDrive/Datasets/DatasetAudios/GTZAN.zip"
with ZipFile(path_zip , 'r') as zip_archive:
    if not os.path.exists("/content/drive/MyDrive/Datasets/DatasetAudios/GTZAN/"):
        zip_archive.extractall("/content/drive/MyDrive/Datasets/DatasetAudios/")
    else:
        print("Arquivo já unzipado, sem necessidade de ações.")

Arquivo já unzipado, sem necessidade de ações.


In [153]:
print(i)

0


## Auxiliar functions of dirs

In [147]:
def dir_genres(path_all_genres : str):
    return [path_all_genres + '/' + pasta for pasta in os.listdir(path_all_genres)]

#Return all files.wav separated per genres
def dir_files_wav(path_genre : str):
  return [path_genre + '/' + arquivo for arquivo in os.listdir(path_genre)]


### Writing on dir :O

In [170]:
def apply_effects(audio, sample_rate):

    transform_set = [audmen.AddGaussianNoise(min_amplitude = 0.002, max_amplitude = 0.003),
                     audmen.Gain(p = 1),
                     audmen.Shift(fade_duration = 0.01, p = 1),
                     audmen.HighPassFilter(p = 1),
                     audmen.LowPassFilter(p = 1),
                     audmen.BitCrush(p = 1),
                     audmen.PolarityInversion(p = 1),
                     audmen.TimeStretch(min_rate = 0.5, max_rate = 1.5, leave_length_unchanged=True, p = 1),
                     audmen.PitchShift(p = 1, min_semitones= -3, max_semitones=3),
                     audmen.Trim(p = 1)
                     ]

    num_new_audios = 5
    new_audios = [audmen.SomeOf(3, transform_set, p = 1)(audio, sample_rate) for i in range(num_new_audios)]

    return new_audios

def write_audios(audios, path, genre, idx, sample_rate):
    for (i, audio) in enumerate(audios):
        idx_string = f"{idx:05d}"  #String format
        new_file = path + "/" + genre +"." + idx_string + ".wav"
        idx = idx+1
        sf.write(new_file, audio, sample_rate)

    return idx
#Writing new audios
def write_new_files_wav(path_genre : str):
    genre = path_genre.split('/')[-1]

    files_from_path = dir_files_wav(path_genre)
    file_index_integer = len(files_from_path)
    if file_index_integer >= 101:
        print(f"Algoritmo já executado para esta pasta: {genre}")
    else:
        for file_wav in files_from_path:
            try:
                audio, sample_rate = librosa.load(file_wav)
                new_audios = apply_effects(audio, sample_rate)
                file_index_integer = write_audios(new_audios, path_genre, genre, file_index_integer, sample_rate)
            except:
                print(f"Arquivo com problema! {file_wav.split('/')[-1]}")

def augmentation(path_root):
    path_from_each_genre = dir_genres(path_root)
    for path_genre in path_from_each_genre:
        write_new_files_wav(path_genre)

augmentation("/content/drive/MyDrive/Datasets/DatasetAudios/GTZAN/Data/genres_original")

Algoritmo já executado par esta pasta: blues
Algoritmo já executado par esta pasta: classical
Algoritmo já executado par esta pasta: country
Algoritmo já executado par esta pasta: disco
Algoritmo já executado par esta pasta: hiphop
Algoritmo já executado par esta pasta: jazz
Algoritmo já executado par esta pasta: metal
Algoritmo já executado par esta pasta: pop
Algoritmo já executado par esta pasta: reggae
Algoritmo já executado par esta pasta: rock


##Making Spectogram

In [ ]:

genres = ["classical", "blues", "country", "disco", "jazz", "hiphop", "metal", "pop", "reggae", "rock"]
path_base = "/content/dataset/GTZAN/Data/genres_original"

# Criando um dicionário com os caminhos dos arquivos de áudio
audio_paths_sample = {genre: f"{path_base}/{genre}/{genre}.00001.wav" for genre in genres}


In [ ]:
Audio(audio_paths_sample["blues"])

In [ ]:
Audio(audio_paths_sample["country"])


In [ ]:
Audio(audio_paths_sample["disco"])


In [ ]:
Audio(audio_paths_sample["jazz"])


In [ ]:
Audio(audio_paths_sample["hiphop"])


In [ ]:
Audio(audio_paths_sample["metal"])


In [ ]:
Audio(audio_paths_sample["pop"])


In [ ]:
Audio(audio_paths_sample["reggae"])


In [ ]:
Audio(audio_paths_sample["rock"])

In [ ]:
def spectro_feat(audio, sample_rate):
  #Transformada de fourier
  FRAME_SIZE = 2048

  HOP_SIZE = 512
  short_fourier_transformed_audio = librosa.stft(audio, n_fft = FRAME_SIZE, hop_length = 512)

  #O audio vira 2d.
  #Primeira dimensão: Faixas de frequecias ((FRAME_SIZE/2)+1)
  #Segunda dimensão: Frames

  #Transformar em valores reais
  escala_Y = np.abs(short_fourier_transformed_audio)**2

  #Converter escala para decibeis
  escala_Y = librosa.power_to_db(escala_Y)
  return escala_Y

def plt_spectogram(audio, sample_rate, y_axis_type= "linear"):
  escala_Y = spectro_feat(audio, sample_rate)
  librosa.display.specshow(escala_Y, sr = sample_rate, x_axis = "time", y_axis = y_axis_type, )
  plt.set_cmap("magma")
  plt.colorbar()

def write_spectrogram(audio, sample_rate, path_write):
  escala_Y = spectro_feat(audio, sample_rate)
  librosa.display.specshow(escala_Y, sr = sample_rate)
  plt.set_cmap("magma")
  plt.savefig(path_write, dpi = 300, bbox_inches = "tight", pad_inches = 0)
  plt.close()

def write_spectrogram_from_genre(files_paths, paths_outputs):
  for (path_file, path_out) in zip(files_paths, paths_outputs):
    audio, sample_rate = librosa.load(path_file)
    write_spectrogram(audio, sample_rate, path_out)
#Writting new images spectogram
def write_all_spectrograms(path_root : str):
  path_genre = path_root + "/genres_original/"
  genres_path = dir_genres(path_genre)

  for genre_path in genres_path:
    files_paths = dir_files_wav(genre_path)
    (numeros) = [file_path.split(".")[1] for file_path in files_paths]
    genero = genre_path.split("/")[-1]
    paths_imgs = [(path_root + "/images/" + genero + "/" + "img." + numero + ".png") for numero in numeros]
    write_spectrogram_from_genre(files_paths, paths_imgs)


 #print(genres_path)

#write_all_spectrograms("/content/dataset/GTZAN/Data")

## Extract Features

## Model

In [ ]:
class genre_classifier(nn.Module):
  def __init__(self):
    super().__init__(self, genre_classifier)


  def forward(self, audio, caracteristic_vector):
    pass


